In [84]:
TGT_CWD = '~/Documents/repos/binance-public-data/python'
import pathlib; import sys

import ibis.interactive; sys.path.append(pathlib.Path(TGT_CWD).expanduser().as_posix())

from rsch.notebook_setup import *
from rsch.lakeshack import LakeShack
import rsch.etl as etl
import rsch.signals as signals
from rsch.universe import Universe, perf_stats

import pyarrow as pa

import ibis
from ibis import _
import ibis.selectors as s
ibis.interactive = True

In [64]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "notebook"
pio.templates.default = 'plotly'
pd.options.plotting.backend = 'plotly'

In [2]:
# ls_path = TGT_CWD + '/data/lakeshack_v2'

ls_path = '/Users/tyler/Documents/repos/binance-public-data/python/data/lakeshack_v3'
ls_path = '/Users/tyler/Documents/repos/binance-public-data/python/data/lakeshack'
ls = LakeShack(ls_path)
ls._update_tables()

unv = Universe(
    bar=ls.to_ibis('um_klines_monthly_1d'),
    selection_secid_count=10
    # bar=ls.to_ibis('um.klines.monthly.1d'),
    
)


apply_universe = True
start_date = '2020-04-01'
# end_date = '2020-12-31'
end_date = '2020-04-30'
# end_date = '2020-06-30'

bar = (
    ls.
    # to_ibis('um.klines.monthly.1m')
    to_ibis('um_klines_monthly_1m')
    .filter(
        (_.close_time <= pd.Timestamp(end_date)) & \
        (_.close_time >= pd.Timestamp(start_date))
    )
)

unvm = Universe(
    bar=bar,
    weights=unv.weights,
    risk_calculation_window=180
)

# unvm = Universe(
#     bar=ls.to_ibis('um.klines.monthly.1m').filter((_.close_time <= pd.Timestamp(end_date))), # & (_.close_time >= pd.Timestamp(start_date)))),
#     weights=unv.weights
# )

/Users/tyler/Documents/repos/binance-public-data/python/rsch/universe.py:192: FutureWarning:

`Table.fillna` is deprecated as of v9.1; use fill_null instead



In [27]:
rt = (
    unvm.bar
    .filter(_['universe_mask'])
    .select(['open_time', 'secid', 'return'])
)

rt = rt.execute().pivot_table(index='open_time', columns='secid', values='return')

In [28]:
rt

secid                BCHUSDT  BNBUSDT  BTCUSDT  EOSUSDT  ETCUSDT  ETHUSDT  \
open_time                                                                   
2020-04-02 00:00:00   0.0053   0.0054   0.0066   0.0058   0.0022   0.0114   
2020-04-02 00:01:00   0.0092   0.0043   0.0039   0.0093   0.0070   0.0034   
2020-04-02 00:02:00   0.0000   0.0003   0.0014   0.0026   0.0008   0.0012   
2020-04-02 00:03:00  -0.0015  -0.0013  -0.0035  -0.0031  -0.0024  -0.0020   
2020-04-02 00:04:00   0.0004  -0.0009   0.0003   0.0013   0.0008   0.0021   
...                      ...      ...      ...      ...      ...      ...   
2020-04-29 23:55:00   0.0000      NaN  -0.0005   0.0000  -0.0009  -0.0003   
2020-04-29 23:56:00   0.0001      NaN   0.0000   0.0003   0.0010   0.0000   
2020-04-29 23:57:00  -0.0003      NaN  -0.0008   0.0003  -0.0009  -0.0001   
2020-04-29 23:58:00   0.0002      NaN   0.0004   0.0000  -0.0001   0.0004   
2020-04-29 23:59:00   0.0008      NaN   0.0014   0.0000   0.0013   0.0003   

secid                LINKUSDT  LTCUSDT  XLMUSDT  XRPUSDT  XTZUSDT  ZECUSDT  
open_time                                                                   
2020-04-02 00:00:00    0.0057   0.0056      NaN   0.0057   0.0062      NaN  
2020-04-02 00:01:00    0.0031   0.0058      NaN   0.0034   0.0056      NaN  
2020-04-02 00:02:00   -0.0004   0.0005      NaN   0.0006   0.0012      NaN  
2020-04-02 00:03:00   -0.0035  -0.0040      NaN  -0.0023   0.0000      NaN  
2020-04-02 00:04:00    0.0035   0.0013      NaN   0.0006   0.0000      NaN  
...                       ...      ...      ...      ...      ...      ...  
2020-04-29 23:55:00   -0.0005   0.0006   0.0001   0.0000   0.0000      NaN  
2020-04-29 23:56:00   -0.0005   0.0002   0.0007   0.0000   0.0007      NaN  
2020-04-29 23:57:00    0.0003  -0.0004  -0.0006   0.0004   0.0000      NaN  
2020-04-29 23:58:00   -0.0008  -0.0004  -0.0001   0.0000   0.0000      NaN  
2020-04-29 23:59:00    0.0000   0.0008   0.0003   0.0009  -0.0003      NaN  

[40320 rows x 12 columns]

In [114]:
periods = pd.period_range(rt.index.min(), rt.index.max(), freq='7D')

p = periods[0]

rt_p = rt.loc[p.start_time:p.end_time].dropna(axis=1, thresh=.8)
corr_p = rt_p.corr()
eigvals, eigvecs = np.linalg.eigh(corr_p)

# reverse the order of the eigveactors and values
eigvals = eigvals[::-1]
eigvecs = eigvecs[:, ::-1]

# now make series and dataframe
eigvals = pd.Series(eigvals)
eigvecs = pd.DataFrame(eigvecs, index=corr_p.columns)

ev_rt = rt_p @ eigvecs

In [115]:
ev_rt[1].corr(ev_rt[1].shift(1))

ev_autocorr = ev_rt.apply(lambda x: x.corr(x.shift(1)))
ev_autocorr

-0.08964923964433813

0    0.0194
1   -0.0896
2   -0.1222
3   -0.2107
4   -0.1994
5   -0.0669
6   -0.2022
7   -0.1118
8   -0.1538
9   -0.0658
dtype: float64

In [116]:
ev_reversal_pnls = {}
for i in range(1, 10):
    ev_reversal_pnls[i] = ev_rt[i].apply(np.sign).shift(1).mul(-1).mul(ev_rt[i])

ev_reversal_pnls = pd.DataFrame(ev_reversal_pnls)

ev_reversal_pnls.cumsum().plot()
ev_reversal_pnls.mean(axis=1).cumsum().plot()
# ev_rt[1].apply(np.sign).shift(1).mul(-1).mul(ev_rt[1]).cumsum().plot()

In [117]:
ev_mod = eigvecs.loc[:, range(1,10)].mean(axis=1)
ev_mod

secid
BCHUSDT     0.0503
BNBUSDT     0.0690
BTCUSDT    -0.0589
EOSUSDT    -0.1818
ETCUSDT    -0.0118
ETHUSDT     0.0717
LINKUSDT   -0.1231
LTCUSDT     0.0954
XRPUSDT     0.1672
XTZUSDT    -0.0990
dtype: float64

In [119]:
ev_mod_rt = rt.loc[periods[1].start_time:periods[1].end_time][ev_mod.index] @ ev_mod
ev_mod_oos_pnl = ev_mod_rt.apply(np.sign).shift(1).mul(-1).mul(ev_mod_rt)

perf_stats(ev_mod_oos_pnl)
ev_mod_oos_pnl.cumsum().plot()

sharpe           71.2542
sortino          99.5826
max_dd           -2.7276
pnl_mean          0.0000
pnl_std           0.0003
pnl_count     10080.0000
pnl_std_err       0.0000
pnl_tstat         9.8676
dtype: float64

In [134]:
ev_mod_rt_rm = ev_mod_rt.rolling(1).mean()
ev_mod_oos_pnl_rm = ev_mod_rt_rm.apply(np.sign).mul(-1).shift(1).mul(ev_mod_rt)

perf_stats(ev_mod_oos_pnl_rm)
ev_mod_oos_pnl_rm.cumsum().plot()

sharpe           71.2542
sortino          99.5826
max_dd           -2.7276
pnl_mean          0.0000
pnl_std           0.0003
pnl_count     10080.0000
pnl_std_err       0.0000
pnl_tstat         9.8676
dtype: float64

In [135]:
sig = ev_mod_rt_rm.apply(np.sign).mul(-1).dropna()
sig
turnover = sig.diff()
tcost_model = 0.0015
tcost = turnover.abs().mul(tcost_model)
pnl_gross = sig.shift(1).mul(ev_mod_rt)
pnl_net = pnl_gross.sub(tcost, fill_value=0)

pnl = pd.DataFrame({'pnl_gross': pnl_gross, 'pnl_net': pnl_net, 'turnover': turnover, 'turnover_cost': turnover_cost})
pnl[['pnl_gross', 'pnl_net']].cumsum().plot()

open_time
2020-04-09 00:00:00   -1.0000
2020-04-09 00:01:00    1.0000
2020-04-09 00:02:00   -1.0000
2020-04-09 00:03:00   -1.0000
2020-04-09 00:04:00   -1.0000
                        ...  
2020-04-15 23:55:00   -1.0000
2020-04-15 23:56:00   -1.0000
2020-04-15 23:57:00    1.0000
2020-04-15 23:58:00    1.0000
2020-04-15 23:59:00   -1.0000
Length: 10080, dtype: float64

In [133]:
tcost.plot()